In [10]:
import nltk
#nltk.download('stopwords')
#nltk.download('wordnet')
from sagemaker.tensorflow import TensorFlow as tf
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
import pandas as pd
import numpy as np
import unicodedata
print("hi")

hi


In [4]:
import boto3
s3=boto3.resource("s3")

embeded_index = dict()

import s3fs
fs = s3fs.S3FileSystem()

# To List 5 files in your accessible bucket
fs.ls('s3://glove-bucket/glove.6B.300d.txt')

# open it directly
i=0
with fs.open(f's3://glove-bucket/glove.6B.300d.txt') as f:
    for line in f:
        values = line.split()
        word = values[0]
        coeff = np.asarray(values[1:],dtype="float32")
        embeded_index[word] = coeff
        i+=1
        print(i,end =" ")
f.close()
#print("hello")
        
            
    #display(Image.open(f))
# import pandas as pd

# bucket='glove-bucket'
# data_key = 'glove.6B.300d.txt'
# # bucket='purvisbcuket3'
# # data_key = 'cancer.csv'
# data_location = 's3://{}/{}'.format(bucket, data_key)


# f=open(data_location)
# pd.read_csv(data_location)

1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89 90 91 92 93 94 95 96 97 98 99 100 101 102 103 104 105 106 107 108 109 110 111 112 113 114 115 116 117 118 119 120 121 122 123 124 125 126 127 128 129 130 131 132 133 134 135 136 137 138 139 140 141 142 143 144 145 146 147 148 149 150 151 152 153 154 155 156 157 158 159 160 161 162 163 164 165 166 167 168 169 170 171 172 173 174 175 176 177 178 179 180 181 182 183 184 185 186 187 188 189 190 191 192 193 194 195 196 197 198 199 200 201 202 203 204 205 206 207 208 209 210 211 212 213 214 215 216 217 218 219 220 221 222 223 224 225 226 227 228 229 230 231 232 233 234 235 236 237 238 239 240 241 242 243 244 245 246 247 248 249 250 251 252 253 254 255 256 257 258 259 260 261 262 263 264 265 266 267 268 269 270 271 272 273 274 275 276 277 

In [11]:


from keras.models import Sequential
from keras.layers import Dense,Dropout,Flatten,Embedding
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.callbacks import EarlyStopping,ModelCheckpoint
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer 
from sklearn.manifold import TSNE


Using TensorFlow backend.


In [12]:
review = pd.read_csv("new_dataset_indian_resto_review.csv")

In [13]:
def find_useful(df):
#     if (df["useful"] == 0) & (df["funny"] == 0) & (df["cool"] == 0):
#         return 0
#     else:
#         return 1
    
    #print(df[4],df[7],df[8])
    if df[4] == 0 and df[7]==0 and df[8] ==0:
        return 0
    else:
        return 1
        
#         return df[4]
#     else:
#         return 1
    


In [14]:
review["label"] = review.apply(find_useful,axis=1)

In [15]:
review.head(2)

Unnamed: 0             business_id                              name  \
0           0  iE71iwcSljg3xm2GB2Y9aA  Marigold Maison- Paradise Valley   
1           1  DJuQgsoj-qmU0i5iTAa4aA                  Tadka Restaurant   

            categories  useful  \
0  Indian, Restaurants       0   
1  Restaurants, Indian       0   

                                                text  stars  funny  cool  \
0  I have been here several times since my last u...    5.0      0     0   
1  We just tried to eat here and I'm pretty sure ...    1.0      1     0   

   label  
0      0  
1      1

In [16]:
review = review[["text","label"]]

In [17]:
review = review.dropna()
review.head(5)
review["label"].value_counts()

1    43195
0    36597
Name: label, dtype: int64

In [18]:
review.head(2)

text  label
0  I have been here several times since my last u...      0
1  We just tried to eat here and I'm pretty sure ...      1

In [19]:
def remove_accents(input_str):
    nfkd_form = unicodedata.normalize('NFKD', input_str)
    only_ascii = nfkd_form.encode('ASCII', 'ignore')
    return only_ascii.decode()
stopwords_ = set(stopwords.words("english"))
lemmatizer=WordNetLemmatizer()

In [20]:
def pre_processing(india_review):
    india_review["normalizes_text"] = india_review["text"].apply(lambda x:remove_accents(x))
    #india_review["remove_html"] = india_review['normalizes_text'].apply(lambda x: strip_html_tags(x))
    india_review["remove_special"] = india_review["normalizes_text"].replace(r'[^A-Za-z0-9 ]+', '', regex=True)
    
    india_review["token_text"] = india_review["remove_special"].apply(lambda x:[word.lower() for word in x.split(" ")]) 
    #india_review["token_text"] = india_review["token_text"].apply(lambda x:[word for word in x if word not in common_words_list])
    
    india_review["remove_stop"] = india_review["token_text"].apply(lambda x:[word for word in x if word not  in stopwords_])
    india_review["lemitize_text"] = india_review["remove_stop"].apply(lambda x: " ".join([lemmatizer.lemmatize(word) for word in x]))
 #   india_review["length"] = india_review["remove_stop"].apply(lambda x:find_length(x))
   # review["clean_list"] = review["lemitize_text"].apply(lambda x:[word for word in x.split(" ")])
#    india_review["texts_to_sequences"] = india_review["lemitize_text"].apply(lambda x:)

    return india_review
     
  
    

In [21]:
review=pre_processing(review)

In [22]:
#review["lemitize_text"]
train_set = review.sample(frac=0.75, random_state=0)
test_set = review.drop(train_set.index)

In [14]:
# # train_review = train_set["lemitize_text"]
# # test_review = test_set["lemitize_text"]
# # train_review.head()
# # label_train = train_set["label"]
# label_test = test_set["label"]



In [15]:
#type(train_review)

In [16]:
#train_review.head(5)

In [25]:
def token_sequence(review):
    max_len=50
    embed_dim=100
    max_words=20000
    tokenizer = Tokenizer(num_words=max_words)
    tokenizer.fit_on_texts(review["lemitize_text"])
    sequences = tokenizer.texts_to_sequences(review["lemitize_text"])
    data = pad_sequences(sequences,maxlen=max_len,padding='post')
    return tokenizer,data
    print(data)

In [27]:
tokenizer_train,train_data=token_sequence(train_set)

In [29]:
tokenizer_test,test_data=token_sequence(test_set)

In [ ]:
def create_label_array(review):
    return np.asarray(review["label"])

In [44]:
train_labels = create_label_array(train_set)
test_labels = create_label_array(test_set)

In [35]:
max_len=50
embed_dim=100
max_words=20000
embeded_matrix = np.zeros((max_words,embed_dim))

In [36]:
for word, i in tokenizer_train.word_index.items():
    if i < max_words:
        embed_vector = embeded_index.get(word)
        if embed_vector is not None:
            embed_matrix[i] = embed_vector

In [37]:
model = Sequential()
model.add(Embedding(max_words,embed_dim,weights = [embeded_matrix],input_length=max_len))

In [38]:
model.add(Flatten())
model.add(Dropout(0.5))
model.add(Dense(32,activation="relu"))
model.add(Dropout(0.5))
model.add(Dense(1,activation="sigmoid"))



Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.


In [39]:
model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_2 (Embedding)      (None, 50, 100)           2000000   
_________________________________________________________________
flatten_3 (Flatten)          (None, 5000)              0         
_________________________________________________________________
dropout_1 (Dropout)          (None, 5000)              0         
_________________________________________________________________
dense_1 (Dense)              (None, 32)                160032    
_________________________________________________________________
dropout_2 (Dropout)          (None, 32)                0         
_________________________________________________________________
dense_2 (Dense)              (None, 1)                 33        
Total params: 2,160,065
Trainable params: 2,160,065
Non-trainable params: 0
_________________________________________________________________


In [42]:
model.compile(loss="binary_crossentropy",optimizer="adam",metrics=["accuracy"])


Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


In [43]:
early_stoping = EarlyStopping(monitor="val_loss",patience=5,mode=min)

/home/ec2-user/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/keras/callbacks.py:511: RuntimeWarning: EarlyStopping mode <built-in function min> is unknown, fallback to auto mode.
  RuntimeWarning)


In [45]:
%%time
model.fit(train_data,train_labels,epochs=20,validation_data=(test_data,test_labels),batch_size=128,verbose=1,callbacks=[early_stoping])



Train on 59844 samples, validate on 19948 samples
Epoch 1/20
59844/59844 [==============================] - 20s 327us/step - loss: 0.6904 - acc: 0.5411 - val_loss: 0.6897 - val_acc: 0.5413
Epoch 2/20
59844/59844 [==============================] - 17s 290us/step - loss: 0.6897 - acc: 0.5414 - val_loss: 0.6897 - val_acc: 0.5413
Epoch 3/20
59844/59844 [==============================] - 17s 291us/step - loss: 0.6897 - acc: 0.5414 - val_loss: 0.6897 - val_acc: 0.5413
Epoch 4/20
59844/59844 [==============================] - 18s 293us/step - loss: 0.6897 - acc: 0.5414 - val_loss: 0.6897 - val_acc: 0.5413
Epoch 5/20
59844/59844 [==============================] - 18s 293us/step - loss: 0.6897 - acc: 0.5414 - val_loss: 0.6897 - val_acc: 0.5413
Epoch 6/20
59844/59844 [==============================] - 17s 292us/step - loss: 0.6897 - acc: 0.5414 - val_loss: 0.6897 - val_acc: 0.5413
Epoch 7/20
59844/59844 [==============================] - 18s 302us/step - loss: 0.6897 - acc: 0.5414 - val_loss: 

In [21]:
len(train_data)


59844

In [22]:
len(test_data)

19948

In [24]:
print(train_data.shape)
print(train_labels.shape)

(59844, 50)
(59844,)


In [25]:
vocab_size_train = len(tokenizer_train.word_index)+1
vocab_size_train

91991

In [26]:
vocab_size_test = len(tokenizer_test.word_index)+1
vocab_size_test

45339

In [27]:
validation_split=0.2
indices = np.arange(train_data.shape[0])

In [28]:
np.random.shuffle(indices)

In [29]:
train_data = train_data[indices]
train_labels = train_labels[indices]

In [30]:
val_samples = int(validation_split*train_data.shape[0])

In [31]:
X_train = train_data[0:-val_samples]
y_train = train_labels[0:-val_samples]
x_val = train_data[-val_samples:]
y_val = train_labels[-val_samples:]

In [34]:
tokenizer_train.word_index.items()

dict_items([('food', 1), ('indian', 2), ('place', 3), ('good', 4), ('chicken', 5), ('restaurant', 6), ('service', 7), ('great', 8), ('time', 9), ('like', 10), ('dish', 11), ('buffet', 12), ('one', 13), ('naan', 14), ('really', 15), ('would', 16), ('go', 17), ('back', 18), ('get', 19), ('ordered', 20), ('order', 21), ('also', 22), ('lunch', 23), ('best', 24), ('curry', 25), ('delicious', 26), ('rice', 27), ('try', 28), ('u', 29), ('nice', 30), ('masala', 31), ('ive', 32), ('dont', 33), ('well', 34), ('menu', 35), ('price', 36), ('come', 37), ('spicy', 38), ('even', 39), ('definitely', 40), ('came', 41), ('little', 42), ('got', 43), ('im', 44), ('love', 45), ('taste', 46), ('always', 47), ('staff', 48), ('make', 49), ('sauce', 50), ('butter', 51), ('first', 52), ('went', 53), ('much', 54), ('table', 55), ('friendly', 56), ('didnt', 57), ('take', 58), ('tikka', 59), ('amazing', 60), ('fresh', 61), ('eat', 62), ('spice', 63), ('dinner', 64), ('never', 65), ('meal', 66), ('lamb', 67), ('thi

In [32]:
embed_index = 

SyntaxError: invalid syntax (<ipython-input-32-fa3f4700dae0>, line 1)

dict_items([('food', 1), ('indian', 2), ('place', 3), ('good', 4), ('chicken', 5), ('restaurant', 6), ('service', 7), ('great', 8), ('time', 9), ('like', 10), ('dish', 11), ('buffet', 12), ('one', 13), ('naan', 14), ('really', 15), ('would', 16), ('go', 17), ('back', 18), ('get', 19), ('ordered', 20), ('order', 21), ('also', 22), ('lunch', 23), ('best', 24), ('curry', 25), ('delicious', 26), ('rice', 27), ('try', 28), ('u', 29), ('nice', 30), ('masala', 31), ('ive', 32), ('dont', 33), ('well', 34), ('menu', 35), ('price', 36), ('come', 37), ('spicy', 38), ('even', 39), ('definitely', 40), ('came', 41), ('little', 42), ('got', 43), ('im', 44), ('love', 45), ('taste', 46), ('always', 47), ('staff', 48), ('make', 49), ('sauce', 50), ('butter', 51), ('first', 52), ('went', 53), ('much', 54), ('table', 55), ('friendly', 56), ('didnt', 57), ('take', 58), ('tikka', 59), ('amazing', 60), ('fresh', 61), ('eat', 62), ('spice', 63), ('dinner', 64), ('never', 65), ('meal', 66), ('lamb', 67), ('thi